In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
need_to_setup_env = False
need_to_setup_env

False

In [5]:
if need_to_setup_env:
    %pip install -r requirements.txt
    %cd /content/
    %rm -rf LLaMA-Factory
    !git clone https://github.com/hiyouga/LLaMA-Factory.git
    %cd LLaMA-Factory
    %ls
    %pip install -e .[torch,bitsandbytes]
    
    os.chdir(workding_dir)
    sys.path.append(workding_dir)
    print("workding dir:", workding_dir)

In [6]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [7]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88 True datasets/mgtv results/mgtv-results_internlm_best.csv


In [8]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 239 ms, sys: 103 ms, total: 342 ms
Wall time: 4.12 s


In [9]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [10]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=adapter_name_or_path, using_llama_factory=True, load_in_4bit=load_in_4bit)

loading model: internlm/internlm2_5-7b-chat-1m with adapter: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88


[INFO|tokenization_utils_base.py:2161] 2024-07-20 13:26:56,525 >> loading file ./tokenizer.model from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/./tokenizer.model
[INFO|tokenization_utils_base.py:2161] 2024-07-20 13:26:56,530 >> loading file added_tokens.json from cache at None
[INFO|tokenization_utils_base.py:2161] 2024-07-20 13:26:56,534 >> loading file special_tokens_map.json from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/special_tokens_map.json
[INFO|tokenization_utils_base.py:2161] 2024-07-20 13:26:56,541 >> loading file tokenizer_config.json from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/tokenizer_config.json
[INFO|tokenization_utils_base.py:2161] 2024-07-20 13:26:56,545 >> loading file tokenize

07/20/2024 13:27:06 - INFO - llamafactory.data.template - Replace eos token: <|im_end|>
07/20/2024 13:27:06 - INFO - llamafactory.data.template - Add <|im_start|> to stop words.


[INFO|configuration_utils.py:733] 2024-07-20 13:27:07,295 >> loading configuration file config.json from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:733] 2024-07-20 13:27:09,367 >> loading configuration file config.json from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:800] 2024-07-20 13:27:09,376 >> Model config InternLM2Config {
  "_name_or_path": "internlm/internlm2_5-7b-chat-1m",
  "architectures": [
    "InternLM2ForCausalLM"
  ],
  "attn_implementation": "eager",
  "auto_map": {
    "AutoConfig": "internlm/internlm2_5-7b-chat-1m--configuration_internlm2.InternLM2Config",
    "AutoModel": "internlm/internlm2_5-7b-chat-1m--modeling_internlm2.InternLM2ForCausalLM",
    "AutoModelForCausalLM": "internlm/internlm2_5-7b

07/20/2024 13:27:09 - INFO - llamafactory.model.model_utils.quantization - Quantizing model to 4 bit with bitsandbytes.
07/20/2024 13:27:09 - INFO - llamafactory.model.patcher - Using KV cache for faster generation.


[INFO|modeling_utils.py:3603] 2024-07-20 13:27:11,102 >> loading weights file model.safetensors from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/model.safetensors.index.json
[INFO|modeling_utils.py:1565] 2024-07-20 13:27:12,118 >> Instantiating InternLM2ForCausalLM model under default dtype torch.bfloat16.
[INFO|configuration_utils.py:1038] 2024-07-20 13:27:12,137 >> Generate config GenerationConfig {
  "bos_token_id": 1,
  "eos_token_id": 2,
  "pad_token_id": 2
}



Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

[INFO|modeling_utils.py:4425] 2024-07-20 14:48:42,924 >> All model checkpoint weights were used when initializing InternLM2ForCausalLM.

[INFO|modeling_utils.py:4433] 2024-07-20 14:48:42,929 >> All the weights of InternLM2ForCausalLM were initialized from the model checkpoint at internlm/internlm2_5-7b-chat-1m.
If your task is similar to the task the model of the checkpoint was trained on, you can already use InternLM2ForCausalLM for predictions without further training.
[INFO|configuration_utils.py:993] 2024-07-20 14:48:43,569 >> loading configuration file generation_config.json from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/generation_config.json
[INFO|configuration_utils.py:1038] 2024-07-20 14:48:43,575 >> Generate config GenerationConfig {
  "bos_token_id": 1,
  "eos_token_id": [
    2,
    92542
  ],
  "pad_token_id": 2
}



07/20/2024 14:48:45 - INFO - llamafactory.model.model_utils.attention - Using vanilla attention implementation.
07/20/2024 14:48:48 - INFO - llamafactory.model.adapter - Loaded adapter(s): llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88
07/20/2024 14:48:48 - INFO - llamafactory.model.loader - all params: 7,756,582,912
CPU times: user 3min 46s, sys: 11min 59s, total: 15min 45s
Wall time: 1h 22min 24s


In [11]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [12]:
def evaluate_model(model, tokenizer, model_name, dataset, batch_size=1):
    print(f"Evaluating model: {model_name} on {device}")
    predictions = eval_model(
        model, tokenizer, dataset, device=device, batch_size=batch_size
    )

    save_results(
        model_name,
        results_path,
        dataset,
        predictions,
        debug=False,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=False)
    print(metrics)

In [13]:
%%time

evaluate_model(model, tokenizer, f"{model_name}_{adapter_name_or_path}_lf_4bit", datasets["test"], batch_size=8)

Evaluating model: internlm/internlm2_5-7b-chat-1m_llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88_lf_4bit on cuda


  0%|          | 0/375 [00:00<?, ?it/s]

  0%|          | 1/375 [24:23<152:05:06, 1463.92s/it]

--------
step 1: 不是
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是
